# Biomass Yield and Spectral Trends

```
date: 2024-12-12
authors:
    - name: Brookie Guzder-Williams
affiliations:
    - University of California Berkeley, The Eric and Wendy Schmidt Center for Data Science & Environment
license: CC-BY-4.0
```

This notebook uses DSE's [Spectral Trend Database](https://github.com/SchmidtDSE/spectral_trend_database) (STDB) to
produce and interactive chart displaying Biomass Yield vs a number of different spectral incides over time.

1. Fetch Data for a random point: We use STDS's [query module](https://github.com/SchmidtDSE/spectral_trend_database/blob/main/spectral_trend_database/query.py) and in particular the [`QueryConstructor`](https://github.com/SchmidtDSE/spectral_trend_database/blob/54146cf058e2180829e2c169b37c18ddf62b68a0/spectral_trend_database/query.py#L21-L114) to generate a ...
2. Build Chart
3. Save Chart JSON to improve responsiveness of chart


---

### IMPORTS


In [1]:
from importlib import reload
from typing import Callable, Union, Optional, Literal, TypeAlias, Sequence, Any
import re
from pprint import pprint
import random
import pandas as pd
import numpy as np
import xarray as xr
import tensorflow as tf
from IPython.display import HTML
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt
from spectral_trend_database.config import config as c
from spectral_trend_database import query
from spectral_trend_database import utils
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import HistGradientBoostingClassifier
from sklearn import metrics


---

### CONFIG

In [2]:
BQ_PREFIX = 'dse-regenag.BiomassTrends'
SAMPLE_FRAC = 0.0005
YEAR_START = 2008
YEAR_END = 2020
START_MMDD = '11-01'
END_MMDD = START_MMDD
ATTR_COLS = [
    'sample_id',
    'lon',
    'lat']
LIST_ATTRS = [
    'year',
    'biomass',
    'crop_type']
CHART_DATA_PATH = 'spectral_trends.chart_data.json'


---

### HELPER METHODS


In [3]:
def print_list(lst, max_len=7, view_size=3, sep=', ', connector=' ... '):
    size = len(lst)
    if size <= max_len:
        lst_str = sep.join(lst)
    else:
        head = sep.join(lst[:view_size])        
        tail = sep.join(lst[-view_size:])
        lst_str = f'{head}{connector}{tail}  [{size}]'
    print(lst_str)

def line(marker='-', length=100):
    print(marker*length)


---

### STDB DATABASE INFO

First we'll take a quick peak at the what is in the STDB database

In [4]:
YIELD_TABLE = 'SCYM_YIELD'
SMOOTHED_INDICES_TABLE = 'SMOOTHED_INDICES_V1'
IDENT_DATE_COLUMNS = ['sample_id', 'year', 'date']

In [5]:
COLUMN_NAMES = {}
print('DATABASE INFO')
line()
query = reload(query)
table_names = query.table_names()
print('TABLES:')
pprint(table_names)
for table_name in [YIELD_TABLE, SMOOTHED_INDICES_TABLE]:
    COLUMN_NAMES[table_name] = query.column_names(table_name, run_query=True)
    print(f'\n{table_name}:')
    print_list(COLUMN_NAMES[table_name])
line()

DATABASE INFO
----------------------------------------------------------------------------------------------------
TABLES:
['SMOOTHED_INDICES_V1',
 'INDICES_STATS_V1',
 'LANDSAT_RAW_MASKED',
 'RAW_INDICES_V1',
 'SAMPLE_POINTS',
 'INDICES_STATS_V1_GROWING_SEASON',
 'INDICES_STATS_V1_OFF_SEASON',
 'ADMINISTRATIVE_BOUNDARIES',
 'SCYM_YIELD',
 'MACD_INDICES_V1']

SCYM_YIELD:
biomass, crop_type, year, sample_id

SMOOTHED_INDICES_V1:
ndbr, ndvi, grvi ... sample_id, rdvi, year  [39]
----------------------------------------------------------------------------------------------------


In [6]:
INDICES = [c for c in COLUMN_NAMES[SMOOTHED_INDICES_TABLE] if c not in IDENT_DATE_COLUMNS]
print_list(INDICES)

ndbr, ndvi, grvi ... si, nli, rdvi  [36]



---

### 1. Fetch Data

In [7]:
qc = query.QueryConstructor('SAMPLE_POINTS', table_prefix=BQ_PREFIX)
qc.select('sample_id')
qc.append(f'WHERE RAND() < {SAMPLE_FRAC}')
sample_ids_df = query.run(sql=qc.sql(), print_sql=True)
sample_ids_df = sample_ids_df.drop_duplicates()
print('nb_samples:', sample_ids_df.shape[0])

[info] spectral_trend_database.query.run: SELECT sample_id FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` WHERE RAND() < 0.0005
nb_samples: 7


In [8]:
def fetch_yield_and_trend_data(
        year_start: int,
        year_end: Optional[int] = None,
        sample_id: Optional[Union[list[str], str]] = None,
        print_sql: Optional[bool] = False,
        limit: Optional[int] = None) -> pd.DataFrame:
    """
    Builds and Executes a SQL Query to get all data
    form a given set of sample_ids during a specified time 
    period.
    
    Args: 
        year_start (int): start year to select data
        year_end (Optional[int] = None): 
            last year to select data from (inclusive). if None use <year_start>
        sample_id (Optional[Union[list[str], str]] = None)
            sample_id or list of sample-ids of data to select. if none select 
            from all samples.
        print_sql (Optional[bool] = False)
        limit (Optional[int] = None)

    Returns:
        pd.DataFrame of smoothed-spectral-indices
    """
    if year_end is None: 
        year_end=year_start
    qc = query.QueryConstructor(
        'SAMPLE_POINTS', 
        table_prefix=BQ_PREFIX,
        using=['sample_id'],  
        how='inner')
    qc.join('SCYM_YIELD')
    qc.join('SMOOTHED_INDICES_V1', 'sample_id', 'year')
    if sample_id:
        if isinstance(sample_id, list):
            sample_id = [f"'{s}'" for s in sample_id]
            sample_ids = f'({", ".join(sample_id)})'
            qc.where(sample_id=sample_ids, sample_id_op='in')
        else:
            qc.where(sample_id=sample_id)
    qc.where('SMOOTHED_INDICES_V1', year=year_start, year_op='>=')
    qc.where('SMOOTHED_INDICES_V1', year=year_end, year_op='<=')
    df = query.run(sql=qc.sql(), print_sql=print_sql)
    return df

In [9]:
data = fetch_yield_and_trend_data(
    year_start=YEAR_START,
    year_end=YEAR_END,
    sample_id=sample_ids_df.sample_id.tolist(),
    print_sql=True)

print('shape:', data.shape)
data.sample(3)

[info] spectral_trend_database.query.run: SELECT * FROM `dse-regenag.BiomassTrends.SAMPLE_POINTS` INNER JOIN `dse-regenag.BiomassTrends.SCYM_YIELD` USING (sample_id) INNER JOIN `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1` USING (sample_id, year) WHERE `dse-regenag.BiomassTrends.SAMPLE_POINTS`.sample_id in ('9zpxd49hkcr', '9zqbzp6tdkp', '9zqr9t90vbr', '9zt03k86xkk', 'dp4brrnpdx0', 'dp5j97c6fcx', 'dphqryhr7vq') AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year >= 2008 AND `dse-regenag.BiomassTrends.SMOOTHED_INDICES_V1`.year <= 2020
shape: (83, 46)


sample_id  year geohash_5 geohash_7  geohash_9        lon        lat  \
32  9zqr9t90vbr  2018     9zqr9   9zqr9t9  9zqr9t90v -92.393390  42.129952   
47  9zt03k86xkk  2011     9zt03   9zt03k8  9zt03k86x -94.163158  42.256618   
62  dp5j97c6fcx  2018     dp5j9   dp5j97c  dp5j97c6f -85.724474  40.362878   

    biomass crop_type                                               ndbr  ...  \
32     3142      corn  [0.7639689641917168, 0.734883411977109, 0.7072...  ...   
47      859       soy  [0.11245156006927816, 0.10359825716548357, 0.0...  ...   
62      884       soy  [0.5890753712779186, 0.6225845992462339, 0.652...  ...   

                                                  msr  \
32  [3.3878782131940617, 3.2010730747395217, 3.022...   
47  [0.40638581925199013, 0.3978698331707063, 0.38...   
62  [1.1535471030204585, 1.4128325941694306, 1.646...   

                                                  tvi  \
32  [1.2000205480744985, 1.1826726915563253, 1.166...   
47  [0.9085686277087993, 0.9056939276665402, 0.902...   
62  [0.8567413755418479, 0.8981995991458146, 0.936...   

                                                  si1  \
32  [-0.5855895875835534, -0.4996107917569647, -0....   
47  [0.08689622506015039, 0.0856921695759996, 0.08...   
62  [0.46924195015217646, 0.4278988890293908, 0.38...   

                                                  rvi  \
32  [18.295291485611074, 17.198378131628132, 16.15...   
47  [1.9824543324499835, 1.9584261514733416, 1.934...   
62  [8.25881853154788, 9.445592374893085, 10.50360...   

                                                 tdvi  \
32  [0.7899792258145959, 0.7610742720216038, 0.733...   
47  [0.1868256422924531, 0.18047292004975146, 0.17...   
62  [0.2832337540975598, 0.3487963153858529, 0.408...   

                                                osavi  \
32  [0.7038196590763549, 0.678112116920561, 0.6533...   
47  [0.2145704715970116, 0.20931329806514473, 0.20...   
62  [0.20849956363966196, 0.26974981693677136, 0.3...   

                                                   si  \
32  [-0.6291974965166518, -0.5387007015864671, -0....   
47  [0.07379627239771146, 0.07229869591704442, 0.0...   
62  [0.4746350559074958, 0.4344853972753913, 0.397...   

                                                  nli  \
32  [0.8558333708523246, 0.8131464262022239, 0.771...   
47  [-0.4262970151294001, -0.4428429976164434, -0....   
62  [0.06617783846873673, 0.17000369746175323, 0.2...   

                                                 date  \
32  [2017-09-04T00:00:00.000000000, 2017-09-05T00:...   
47  [2010-09-08T00:00:00.000000000, 2010-09-09T00:...   
62  [2017-09-01T00:00:00.000000000, 2017-09-02T00:...   

                                                 rdvi  
32  [0.6473843688900706, 0.6244825405405395, 0.602...  
47  [0.1806563310182935, 0.17581071255622543, 0.17...  
62  [0.22205766036751493, 0.2762468029232154, 0.32...  

[3 rows x 46 columns]

In [10]:
rows = data[data.sample_id == data.sample().sample_id.iloc[0]]
rows = rows.sort_values('year').reset_index(drop=True)

In [11]:
utils = reload(utils)
def filter_dates(row):
    return dict(date=slice(f'{row.year-1}-{START_MMDD}', f'{row.year}-{END_MMDD}'))
    
ds = utils.rows_to_xr(
    rows, 
    coord='date', 
    sel=filter_dates, 
    attr_cols=ATTR_COLS,
    list_attrs=LIST_ATTRS)
ds

<xarray.Dataset>
Dimensions:   (date: 4395)
Coordinates:
  * date      (date) datetime64[ns] 2007-11-01 2007-11-02 ... 2019-11-01
Data variables: (12/36)
    ndbr      (date) float64 -0.0225 -0.01478 -0.007159 ... 0.04627 0.02765
    ndvi      (date) float64 0.175 0.1645 0.1536 ... 0.1169 0.09616 0.07281
    grvi      (date) float64 1.908 1.836 1.766 1.701 ... 1.75 1.716 1.674 1.624
    ndwi      (date) float64 -0.2767 -0.2618 -0.2463 ... -0.2566 -0.2461 -0.2338
    slavi     (date) float64 0.5673 0.566 0.5648 0.5639 ... 0.6084 0.5913 0.5722
    ndmi      (date) float64 -0.1455 -0.1347 -0.1237 ... -0.0653 -0.078 -0.08984
    ...        ...
    rvi       (date) float64 1.476 1.438 1.401 1.366 ... 1.422 1.375 1.318 1.253
    tdvi      (date) float64 0.1159 0.1126 0.109 0.105 ... 0.1147 0.1057 0.09557
    osavi     (date) float64 0.1166 0.1106 0.1042 ... 0.09839 0.08608 0.07215
    si        (date) float64 0.3188 0.3446 0.3695 ... 0.2021 0.2029 0.2053
    nli       (date) float64 -0.354 -0.337 -0.3202 ... -0.4639 -0.4751 -0.4867
    rdvi      (date) float64 0.1067 0.1025 0.09797 ... 0.0962 0.08646 0.07544
Attributes:
    sample_id:  dphqryhr7vq
    lon:        -83.6768550402
    lat:        40.507865209
    year:       [2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, ...
    biomass:    [2084, 660, 796, 885, 1200, 627, 729, 566, 2763, 472, 827, 450]
    crop_type:  ['corn', 'soy', 'soy', 'soy', 'corn', 'soy', 'soy', 'soy', 'c...

In [12]:
yield_biomass = { y: b for y,b in zip(ds.year, ds.biomass)}
crop_types = { y: b for y,b in zip(ds.year, ds.crop_type)}
dvars = { k: ds[k].data for k in ds.data_vars }
_df = pd.DataFrame(dvars)
_df['date'] = ds.date.data
_df['idx'] = list(_df.index)
_df['year'] = _df.date.apply(lambda d: d.year)
_df['biomass'] = _df.year.apply(lambda y: yield_biomass.get(y, None))
_df['crop_type'] = _df.year.apply(lambda y: crop_types.get(y, 'soy'))

In [13]:
_df.date.astype(str)

0       2007-11-01
1       2007-11-02
2       2007-11-03
3       2007-11-04
4       2007-11-05
           ...    
4390    2019-10-28
4391    2019-10-29
4392    2019-10-30
4393    2019-10-31
4394    2019-11-01
Name: date, Length: 4395, dtype: object

In [14]:
# _df['date'] = _df.date.astype(str).apply(lambda d: f'{d}T00:00:01.000Z')
# _df['date'] = pd.to_datetime(_df.date.astype(str))
# _df.to_json(CHART_DATA_PATH, orient='records', lines=False)


---

### CHART

In [15]:
S = 1.25
DEFAULT_INDEX = 'ndvi'
HEIGHT = 400 * S
GRAPH_WIDTH = 600 * S
SI_COLOR = '#515e68'
SI_OPACITY = 0.6
YIELD_OPACITY = 0.5
TITLE_COLOR = '#333'
TITLE_SIZE = 22
TITLE_WEIGHT = 200
SUBTITLE_COLOR = '#aaa'
SUBTITLE_SIZE = 14
SOY_COLOR = '#4e9561'
CORN_COLOR = '#e2d644'

In [16]:
TITLE = 'SPECTRAL TRENDS'
SUBTITLE = 'exploring yield as a function of spectral indices'

In [17]:
chart_data = _df
# chart_data = CHART_DATA_PATH

In [18]:
#| label: nb.indices_vs_yield
#| placeholder: ./images/TBD.png

# alt.data_transformers.enable("vegafusion")

display(HTML("""
<style>
  span.vega-bind-name {
    color: #555;
    margin: 0 10px 0 60px;
    font-size: 20px;
  }
  .vega-bind label select {
    color: #555;
    font-size: 18px;
  }
</style>
"""))

# yield chart
yield_scale = alt.Scale(
    domain=[0.0, 3000],
    clamp=True
)
yield_color_scale = alt.Scale(
    domain=['soy', 'corn'], 
    range=[SOY_COLOR, CORN_COLOR])
yield_yaxis = alt.Axis(title='Biomass Yield', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
yield_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('biomass:Q', axis=yield_yaxis, scale=yield_scale),
    color=alt.Color('crop_type:N', scale=yield_color_scale)
).mark_area(
    filled=True,
    opacity=YIELD_OPACITY,
    interpolate='step-before')

# interactive spectral index chart
si_yaxis = alt.Axis(title='Spectral Index', titleFontSize=18, titleColor=TITLE_COLOR, titleFontWeight=TITLE_WEIGHT)
si_dropdown = alt.binding_select(
    options=INDICES,
    labels=[n.upper() for n in INDICES],
    name='Spectral Index: '.upper()
)
ycol_param = alt.param(
    value=DEFAULT_INDEX,
    bind=si_dropdown
)
si_chart = alt.Chart(chart_data).encode(
    x=alt.X('date:T', title=None),
    y=alt.Y('y:Q', axis=si_yaxis)
).properties(
    width=GRAPH_WIDTH,
    height=HEIGHT
).transform_calculate(
    y=f'datum[{ycol_param.name}]'
).add_params(
    ycol_param
).mark_area(
    fill=SI_COLOR,
    fillOpacity=SI_OPACITY
)

# display
title = alt.Title(
    TITLE,
    color=TITLE_COLOR,
    fontSize=TITLE_SIZE,
    fontWeight=TITLE_WEIGHT,
    subtitle=SUBTITLE,
    subtitleColor=SUBTITLE_COLOR,
    subtitleFontSize=SUBTITLE_SIZE)

chart = alt.layer(yield_chart, si_chart).resolve_scale(y='independent')
chart = chart.properties(
    title=title).configure_legend(
    title=None,
    labelFontSize=18,  
    labelColor=SUBTITLE_COLOR 
).interactive()
chart 

alt.LayerChart(...)